In [1]:
import torch
import numpy as np
from torch import nn
from dataset import *
import torch.nn.functional as F
from torchvision import transforms
from torch.utils.data import Dataset
from torchvision import datasets
import pandas as pd
from torchvision.transforms import ToTensor
from mylib import *
from skimage import io as skio 
import matplotlib.pyplot as plt
class PixelNorm(nn.Module):
    def forward(self, x):
        eps = 1e-7
        mean = torch.mean(x**2, dim=1, keepdims=True)
        return x / (torch.sqrt(mean)+eps)

/home/matsuda/anaconda3/envs/matsuda_project/lib/python3.8/site-packages/gensim/similarities/__init__.py:15: UserWarning: The gensim.similarities.levenshtein submodule is disabled, because the optional Levenshtein package <https://pypi.org/project/python-Levenshtein/> is unavailable. Install Levenhstein (e.g. `pip install python-Levenshtein`) to suppress this warning.
  warnings.warn(msg)


In [2]:
class WeightScale(nn.Module):
    def forward(self, x, gain=2):
        scale = (gain/x.shape[1])**0.5
        return x * scale

In [3]:
class MiniBatchStd(nn.Module):
    def forward(self, x):
        std = torch.std(x, dim=0, keepdim=True)
        mean = torch.mean(std, dim=(1,2,3), keepdim=True)
        n,c,h,w = x.shape
        mean = torch.ones(n,1,h,w, dtype=x.dtype, device=x.device)*mean
        return torch.cat((x,mean), dim=1)

In [4]:
class Conv2d(nn.Module):
    def __init__(self, inch, outch, kernel_size, padding=0):
        super().__init__()
        self.layers = nn.Sequential(
            WeightScale(),
            nn.ReflectionPad2d(padding),
            nn.Conv2d(inch, outch, kernel_size, padding=0),
            PixelNorm(),
            )
        nn.init.kaiming_normal_(self.layers[2].weight)

    def forward(self, x):
        return self.layers(x)

In [5]:
class ConvModuleG(nn.Module):
    '''
    Args:
        out_size: (int), Ex.: 16 (resolution)
        inch: (int),  Ex.: 256
        outch: (int), Ex.: 128
    '''
    def __init__(self, out_size, inch, outch, first=False):
        super().__init__()

        if first:
            layers = [
                Conv2d(inch, outch, 3, padding=1),
                nn.LeakyReLU(0.2, inplace=False),
                Conv2d(outch, outch, 3, padding=1),
                nn.LeakyReLU(0.2, inplace=False),
            ]

        else:
            layers = [
                nn.Upsample((out_size, out_size), mode='nearest'),
                Conv2d(inch, outch, 3, padding=1),
                nn.LeakyReLU(0.2, inplace=False),
                Conv2d(outch, outch, 3, padding=1),
                nn.LeakyReLU(0.2, inplace=False),
            ]

        self.layers = nn.Sequential(*layers)

    def forward(self, x):
        return self.layers(x)

In [6]:
class ConvModuleD(nn.Module):
    '''
    Args:
        out_size: (int), Ex.: 16 (resolution)
        inch: (int),  Ex.: 256
        outch: (int), Ex.: 128
    '''
    def __init__(self, out_size, inch, outch, final=False):
        super().__init__()
        self.final = final
        if final:
            layers = [
                MiniBatchStd(), # final block only
                Conv2d(inch+1, outch, 3, padding=1),
                nn.LeakyReLU(0.2, inplace=False),
                Conv2d(outch, outch, 4, padding=0), 
                nn.LeakyReLU(0.2, inplace=False), 
            ]
            layer_TF = [nn.Conv2d(outch, 1, 1, padding=0)]
            layer_char = [nn.Conv2d(outch, 26, 1, padding=0)]
            
            self.layer_TF = nn.Sequential(*layer_TF)
            self.layer_char = nn.Sequential(*layer_char)
        else:
            layers = [
                Conv2d(inch, outch, 3, padding=1),
                nn.LeakyReLU(0.2, inplace=False),
                Conv2d(outch, outch, 3, padding=1),
                nn.LeakyReLU(0.2, inplace=False),
                nn.AdaptiveAvgPool2d((out_size, out_size)),
            ]

        self.layers = nn.Sequential(*layers)
    def forward(self, x):
        x = self.layers(x)
        if self.final:
            x_TF = torch.squeeze(self.layer_TF(x))
            x_char = torch.squeeze(self.layer_char(x))
        else:
            x_TF = x
            x_char = None
        return x_TF, x_char

In [7]:
class Generator(nn.Module):
    def __init__(self):
        super().__init__()

        # conv modules & toRGBs
        scale = 1
        inchs  = np.array([512 + 26,256,128,64,32,16], dtype=np.uint32)*scale
        outchs = np.array([256,128, 64,32,16, 8], dtype=np.uint32)*scale
        sizes = np.array([4,8,16,32,64,128], dtype=np.uint32)
        firsts = np.array([True, False, False, False, False, False], dtype=np.bool)
        blocks, toRGBs = [], []
        for s, inch, outch, first in zip(sizes, inchs, outchs, firsts):
            blocks.append(ConvModuleG(s, inch, outch, first))
            toRGBs.append(nn.Conv2d(outch, 1, 1, padding=0))

        self.blocks = nn.ModuleList(blocks)
        self.toRGBs = nn.ModuleList(toRGBs)

    def forward(self, x, y_char, res, eps=1e-7):
        # to image
        n,c = x.shape
        x = x.reshape(n,c//16,4,4)
        y_char = y_char.reshape(y_char.size(0), y_char.size(1), 1, 1)
        y_char = y_char.expand(y_char.size(0), y_char.size(1),4,4)
        # for the highest resolution
        x = torch.cat([x, y_char], axis = 1)
        res = min(res, len(self.blocks))

        # get integer by floor
        nlayer = max(int(res-eps), 0)
        for i in range(nlayer):
            x = self.blocks[i](x)

        # high resolution
        x_big = self.blocks[nlayer](x)
        dst_big = self.toRGBs[nlayer](x_big)

        if nlayer==0:
            x = dst_big
        else:
            # low resolution
            x_sml = F.interpolate(x, x_big.shape[2:4], mode='nearest')
            dst_sml = self.toRGBs[nlayer-1](x_sml)
            alpha = res - int(res-eps)
            x = (1-alpha)*dst_sml + alpha*dst_big

        #return x, n, res
        return torch.sigmoid(x)

In [8]:
class Discriminator(nn.Module):
    def __init__(self):
        super().__init__()

        self.minbatch_std = MiniBatchStd()

        # conv modules & toRGBs
        scale = 1
        inchs = np.array([256,128, 64,32,16, 8], dtype=np.uint32)*scale
        outchs  = np.array([512,256,128,64,32,16], dtype=np.uint32)*scale
        sizes = np.array([1,4,8,16,32,64], dtype=np.uint32)
        finals = np.array([True, False, False, False, False, False], dtype=np.bool)
        blocks, fromRGBs = [], []
        for s, inch, outch, final in zip(sizes, inchs, outchs, finals):
            fromRGBs.append(nn.Conv2d(1, inch, 1, padding=0))
            blocks.append(ConvModuleD(s, inch, outch, final=final))

        self.fromRGBs = nn.ModuleList(fromRGBs)
        self.blocks = nn.ModuleList(blocks)

    def forward(self, x, res):
        # for the highest resolution
        res = min(res, len(self.blocks))

        # get integer by floor
        eps = 1e-7
        n = max(int(res-eps), 0)

        # high resolution
        x_big = self.fromRGBs[n](x)
        x_big, char = self.blocks[n](x_big)

        if n==0:
            x = x_big
        else:
            # low resolution
            x_sml = F.adaptive_avg_pool2d(x, x_big.shape[2:4])
            x_sml = self.fromRGBs[n-1](x_sml)
            alpha = res - int(res-eps)
            x = (1-alpha)*x_sml + alpha*x_big

        for i in range(n):
            x, char = self.blocks[n-1-i](x)

        return x, char

In [9]:
def gradient_penalty(netD, real, fake, res, batch_size, gamma=1):
    device = real.device
    alpha = torch.rand(batch_size, 1, 1, 1, requires_grad=True).to(device)
    x = alpha*real + (1-alpha)*fake
    d_, _ = netD.forward(x, res)
    g = torch.autograd.grad(outputs=d_, inputs=x,
                            grad_outputs=torch.ones(d_.shape).to(device),
                            create_graph=True, retain_graph=True,only_inputs=True)[0]
    g = g.reshape(batch_size, -1)
    return ((g.norm(2,dim=1)/gamma-1.0)**2).mean()

In [10]:
from options import *
parser = get_parser()
opts = parser.parse_args(args=[])
data = np.array([np.load(d) for d in opts.data])
ID = {key:idx+1 for idx, key in enumerate(opts.w2v_vocab)}
weights = np.array(list(opts.w2v_vocab.values()))
impression_word_list = opts.impression_word_list
char_num = opts.char_num
SEED = 42
random.seed(SEED)
np.random.seed(SEED)
torch.manual_seed(SEED)
torch.cuda.manual_seed(SEED)
torch.backends.cudnn.deterministic = True

In [11]:
log_dir = os.path.join(opts.root, opts.dt_now)
check_point_dir = os.path.join(log_dir, 'check_points')
output_dir = os.path.join(log_dir, 'output')
weight_dir = os.path.join(log_dir, 'weight')
logs_GAN = os.path.join(log_dir, "learning_image")
learning_log_dir = os.path.join(log_dir, "learning_log")
if not os.path.exists(log_dir):
    os.makedirs(check_point_dir)
if not os.path.exists(check_point_dir):
    os.makedirs(check_point_dir)
if not os.path.exists(output_dir):
    os.makedirs(output_dir)
if not os.path.exists(weight_dir):
    os.makedirs(weight_dir)
if not os.path.exists(logs_GAN):
    os.makedirs(logs_GAN)
if not os.path.exists(learning_log_dir):
    os.makedirs(learning_log_dir)

In [ ]:
if __name__ == '__main__':
    device = 'cuda' if torch.cuda.is_available() else 'cpu'

    netG = Generator().to(device)
    netD = Discriminator().to(device)
    netG_mavg = Generator().to(device) # moving average
    if opts.device_count > 1:
        netD = nn.DataParallel(netD)
        netG = nn.DataParallel(netG)
        netG_mavg = nn.DataParallel(netG_mavg)
    optG = torch.optim.Adam(netG.parameters(), lr=0.0002, betas=(0.0, 0.99))
    optD = torch.optim.Adam(netD.parameters(), lr=0.0002, betas=(0.0, 0.99))
    criterion = torch.nn.BCELoss()

    # dataset
    transform = transforms.Compose([])

    trainset = Myfont_dataset2(data, impression_word_list, ID, char_num=char_num,
                                  transform=transform)

    bs = 128  ##32
    train_loader = torch.utils.data.DataLoader(trainset, batch_size=bs, shuffle=True,
                                                 collate_fn=collate_fn, drop_last=True)
    
    # training
    nepoch = 100000
    losses = []
    res_step = 10000  ##10000
    j = 0
    # constant random inputs
    z0 = torch.randn(4, 512*16)
    z0 = torch.clamp(z0, -1.,1.)
    z0 = tile(z0, 0, 26).to(device)
    for iepoch in range(nepoch):
        if j==res_step*6.5:
            optG.param_groups[0]['lr'] = 0.0001
            optD.param_groups[0]['lr'] = 0.0001

        for i, d in enumerate(train_loader):
            x, y_char = d["img_target"]/255, d['charclass_target']
            x = x.to(device)
            y_char = torch.eye(26)[y_char].to(device)
            res = j/res_step

            ### train generator ###
            z = torch.randn(bs, 512*16).to(x.device)
            x_ = netG.forward(z, y_char, res)
            d_, d_char = netD.forward(x_, res) # fake
            print(y_char.shape)
            G_char_loss = kl_divergence(d_char, y_char, activation = 'softmax')
            G_TF_loss = -d_.mean() # WGAN_GP
            G_loss = G_char_loss +  G_TF_loss 
            optG.zero_grad()
            G_loss.backward()
            optG.step()

            # update netG_mavg by moving average
            momentum = 0.995 # remain momentum
            alpha = min(1.0-(1/(j+1)), momentum)
            for p_mavg, p in zip(netG_mavg.parameters(), netG.parameters()):
                p_mavg.data = alpha*p_mavg.data + (1.0-alpha)*p.data

            ### train discriminator ###
            for _ in range(1):
                z = torch.randn(x.shape[0], 512*16).to(x.device)
                x_ = netG.forward(z, y_char, res)
                x = F.adaptive_avg_pool2d(x, x_.shape[2:4])
                d, d_char = netD.forward(x, res)   # real
                d_, _ = netD.forward(x_, res) #fake
                loss_real = -d.mean()
                loss_fake = d_.mean()
                D_char_loss = kl_divergence(d_char, y_char, activation = 'softmax')
                loss_gp = gradient_penalty(netD, x.data, x_.data, res, x.shape[0])
                loss_drift = (d**2).mean()

                beta_gp = 10.0
                beta_drift = 0.001
                D_TF_loss = loss_real + loss_fake + beta_gp*loss_gp + beta_drift*loss_drift
                D_loss = D_TF_loss + D_char_loss
                optD.zero_grad()
                D_loss.backward()
                optD.step()
            ##caliculate accuracy
            real_pred = 1 * (F.sigmoid(d) > 0.5).detach().cpu()
            fake_pred = 1 * (F.sigmoid(d_) > 0.5).detach().cpu()
            real_TF = torch.ones(real_pred.size(0))
            fake_TF = torch.zeros(fake_pred.size(0))
            real_acc = (real_pred ==real_TF).float().sum().item()/len(real_pred)
            fake_acc = (fake_pred == fake_TF).float().sum().item()/len(fake_pred)
            print('ep: %02d %04d %04d lossG=%.10f lossD=%.10f lossGChar=%.10f lossDChar=%.10f real_acc=%.10f fake_acc=%.10f' %
                  (iepoch, i, j, G_TF_loss.item(), D_TF_loss.item(), G_char_loss.item(), D_char_loss.item(), real_acc, fake_acc))
            print(x.shape)
            losses.append([G_TF_loss.item(), D_TF_loss.item(), G_char_loss.item(), D_char_loss.item(), real_acc, fake_acc])
            j += 1

            if j%500==0:
                netG_mavg.eval()
                z = torch.randn(4, 512*16)
                z = tile(z, 0, 26).to(x.device)
                y_char = torch.eye(26).repeat(4,1).to(x.device)
                x_0 = netG_mavg.forward(z0, y_char, res)
                x_ = netG_mavg.forward(z, y_char, res)

                dst = torch.cat((x_0, x_), dim=0)
                dst = F.interpolate(dst, (128, 128), mode='nearest')
                dst = dst.to('cpu').detach()
                n, c, h, w = dst.shape
#                 dst = dst.reshape(4,8,c,h,w)
#                 dst = dst.transpose(0,3,1,4,2)
#                 dst = dst.reshape(4*h,8*w,1)
#                 dst = torch.clamp(dst*255., 0, 255)
                save_image(dst, os.path.join(logs_GAN, 'img_%03d_%05d.png' % (iepoch, j)), nrow= 26)
#                 skio.imsave('out/img_%03d_%05d.png' % (iepoch, j), dst)
                losses_ = np.array(losses)
                history_loss = {'D_TF_loss': losses_[:, 0].tolist(),
                'G_TF_loss': losses_[:, 1].tolist(),
                'D_class_loss': losses_[:, 2].tolist(),
                'G_class_loss': losses_[:, 3].tolist()}
                history_acc = {"real_acc": losses_[:, 4].tolist(),
                'fake_acc': losses_[:, 5].tolist(),}    
                learning_curve(history_loss, os.path.join(learning_log_dir, 'loss_{:03d}_{:05d}'.format(iepoch, j)))
                learning_curve(history_acc, os.path.join(learning_log_dir, 'acc_{:03d}_{:05d}'.format(iepoch, j)))
#                 losses_ = np.array(losses)
#                 niter = losses_.shape[0]//100*100
#                 x_iter = np.arange(100)*(niter//100) + niter//200
#                 plt.plot(x_iter, losses_[:niter,0].reshape(100,-1).mean(1))
#                 plt.plot(x_iter, losses_[:niter,1].reshape(100,-1).mean(1))
#                 plt.tight_layout()
#                 plt.savefig('out/loss_%03d_%05d.png' % (iepoch, j))
#                 plt.clf()

                netG_mavg.train()

            if j >= res_step*7:
                break

#             if j%100==0:
#                 coolGPU()

        if j >= res_step*7:
            break

<ipython-input-7-febd7903541a>:10: DeprecationWarning: `np.bool` is a deprecated alias for the builtin `bool`. To silence this warning, use `bool` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.bool_` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  firsts = np.array([True, False, False, False, False, False], dtype=np.bool)
<ipython-input-8-7bdd32832c5d>:12: DeprecationWarning: `np.bool` is a deprecated alias for the builtin `bool`. To silence this warning, use `bool` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.bool_` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  finals = np.array([True, False, False, False, False, False], dtype=np.bool)
100%|██████████| 17202/17202 [00:03<

torch.Size([128, 26])
ep: 00 0000 0000 lossG=0.1120603979 lossD=3.5350172520 lossGChar=3.3526427746 lossDChar=3.3464937210 real_acc=0.0078125000 fake_acc=1.0000000000
torch.Size([128, 1, 4, 4])
torch.Size([128, 26])
ep: 00 0001 0001 lossG=0.6212646961 lossD=30.3389282227 lossGChar=3.3265371323 lossDChar=3.3580787182 real_acc=0.1406250000 fake_acc=0.9765625000
torch.Size([128, 1, 4, 4])
torch.Size([128, 26])


/home/matsuda/anaconda3/envs/matsuda_project/lib/python3.8/site-packages/torch/nn/functional.py:1709: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


ep: 00 0002 0002 lossG=0.2979431748 lossD=4.9103565216 lossGChar=3.3096182346 lossDChar=3.3147630692 real_acc=0.0000000000 fake_acc=1.0000000000
torch.Size([128, 1, 4, 4])
torch.Size([128, 26])
ep: 00 0003 0003 lossG=0.3506296873 lossD=2.3147959709 lossGChar=3.3007028103 lossDChar=3.2968246937 real_acc=0.0000000000 fake_acc=1.0000000000
torch.Size([128, 1, 4, 4])
torch.Size([128, 26])
ep: 00 0004 0004 lossG=0.3619205654 lossD=0.7401255965 lossGChar=3.3055865765 lossDChar=3.2953655720 real_acc=0.0000000000 fake_acc=1.0000000000
torch.Size([128, 1, 4, 4])
torch.Size([128, 26])
ep: 00 0005 0005 lossG=0.3740457296 lossD=0.1913304925 lossGChar=3.2812051773 lossDChar=3.2704930305 real_acc=0.0000000000 fake_acc=1.0000000000
torch.Size([128, 1, 4, 4])
torch.Size([128, 26])
ep: 00 0006 0006 lossG=0.4133295119 lossD=0.0885455012 lossGChar=3.3257961273 lossDChar=3.3268957138 real_acc=0.0156250000 fake_acc=1.0000000000
torch.Size([128, 1, 4, 4])
torch.Size([128, 26])
ep: 00 0007 0007 lossG=0.44170

/home/matsuda/anaconda3/envs/matsuda_project/lib/python3.8/site-packages/torch/nn/functional.py:1709: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


...

ep: 10 2281 37001 lossG=0.8138748407 lossD=-2.8591752052 lossGChar=0.1356151998 lossDChar=0.4859493077 real_acc=0.8671875000 fake_acc=0.5390625000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 2282 37002 lossG=2.3819904327 lossD=-2.8806927204 lossGChar=0.2140217274 lossDChar=0.5196021795 real_acc=0.7812500000 fake_acc=0.7578125000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 2283 37003 lossG=7.3498611450 lossD=-1.9570981264 lossGChar=0.1951127946 lossDChar=0.5588594079 real_acc=0.0703125000 fake_acc=1.0000000000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 2284 37004 lossG=0.3056376576 lossD=-2.3477988243 lossGChar=0.2833619714 lossDChar=0.6451227069 real_acc=0.9140625000 fake_acc=0.3437500000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 2285 37005 lossG=6.8461694717 lossD=-2.2323164940 lossGChar=0.1505659223 lossDChar=0.4821394980 real_acc=0.1484375000 fake_acc=1.0000000000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 228

/home/matsuda/anaconda3/envs/matsuda_project/lib/python3.8/site-packages/torch/nn/functional.py:1709: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


ep: 10 2781 37501 lossG=2.9304089546 lossD=-2.6343035698 lossGChar=0.1729371250 lossDChar=0.2893149555 real_acc=0.6406250000 fake_acc=0.8203125000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 2782 37502 lossG=5.2693080902 lossD=-2.6710863113 lossGChar=0.2454212606 lossDChar=0.4602626860 real_acc=0.2421875000 fake_acc=1.0000000000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 2783 37503 lossG=4.7584586143 lossD=-2.4909486771 lossGChar=0.1301663518 lossDChar=0.4411033988 real_acc=0.3437500000 fake_acc=1.0000000000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 2784 37504 lossG=3.2000002861 lossD=-2.0325002670 lossGChar=0.2405972779 lossDChar=0.6688252091 real_acc=0.4140625000 fake_acc=0.8671875000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 2785 37505 lossG=4.1937041283 lossD=-2.9689981937 lossGChar=0.1321589351 lossDChar=0.5083215237 real_acc=0.5156250000 fake_acc=0.8750000000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 278

/home/matsuda/anaconda3/envs/matsuda_project/lib/python3.8/site-packages/torch/nn/functional.py:1709: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


ep: 10 3281 38001 lossG=2.5127639771 lossD=-3.0099818707 lossGChar=0.2241926044 lossDChar=0.2734416723 real_acc=0.6953125000 fake_acc=0.8750000000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 3282 38002 lossG=2.4120903015 lossD=-2.2436687946 lossGChar=0.2419299483 lossDChar=0.4963675439 real_acc=0.6093750000 fake_acc=0.8593750000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 3283 38003 lossG=4.9650983810 lossD=-2.1341843605 lossGChar=0.2093249857 lossDChar=0.4276363552 real_acc=0.1718750000 fake_acc=1.0000000000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 3284 38004 lossG=0.3307940364 lossD=-2.1081805229 lossGChar=0.3556432724 lossDChar=0.3588268459 real_acc=0.9062500000 fake_acc=0.4062500000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 3285 38005 lossG=7.7550926208 lossD=-1.8642698526 lossGChar=0.2694357038 lossDChar=0.3643953204 real_acc=0.0000000000 fake_acc=1.0000000000
torch.Size([128, 1, 32, 32])
torch.Size([128, 26])
ep: 10 328

In [ ]:
!pip install coolGPU2

